[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/galaxyproject/SARS-CoV-2/blob/master/data/ipynb/intrahost.ipynb)


# Analysis of intra-host data

Feb 22, 2021 / This notebook is WIP

## Prepping the notebook

In [ ]:
!pip3 install -U datapane

     |████████████████████████████████| 1.2MB 5.6MB/s 
     |████████████████████████████████| 20.7MB 1.3MB/s 
     |████████████████████████████████| 102kB 12.1MB/s 
     |████████████████████████████████| 8.9MB 44.8MB/s 
     |████████████████████████████████| 2.2MB 49.7MB/s 
  Created wheel for bokeh: filename=bokeh-2.2.3-cp36-none-any.whl size=9296311 sha256=d87676086ab8f4de6a90ad9ccc47b3f072dbf5539aed6a1506f8481be6b2e38e
  Stored in directory: /root/.cache/pip/wheels/dc/96/7b/9c9d48ed392511bc708e39580e18dc7a92f475795cd26b51bf
Successfully built bokeh
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.12.1 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: importlib-resources 3.3.1
    Uninstalling importlib-resources-3.3.1:
      Successfully uninstalled importlib-resources-3.3.1
  Found existing installation: pyarrow 2.0.0
    Un

In [1]:
from datetime import date
print(date.today())

2021-02-22


In [ ]:
import datapane as dp

In [ ]:
# Set you datapane.com access token here
dp.login(token="xxxxx")

Connected successfully to https://datapane.com as nekrut


In [2]:
# Update necessary packages
!pip install --upgrade biopython pandasql

     |████████████████████████████████| 2.3MB 4.8MB/s 
  Created wheel for pandasql: filename=pandasql-0.7.3-cp36-none-any.whl size=26820 sha256=c79340cfcb0cfe95756783eae8ba67989a9a34db480e986df214fc9b5d8feb5a
  Stored in directory: /root/.cache/pip/wheels/53/6c/18/b87a2e5fa8a82e9c026311de56210b8d1c01846e18a9607fc9
Successfully built pandasql


In [3]:
# Our main plotting package (must have explicit import of submodules)
import bokeh.io
import bokeh.plotting
from bokeh.models import ColumnDataSource,Quad,Range1d,Band,Rect,BoxAnnotation
from bokeh.plotting import figure, show,output_file
from bokeh.palettes import Set1_7,Reds

from bokeh.layouts import gridplot,column

set17 = Set1_7

# Enable viewing Bokeh plots in the notebook
bokeh.io.output_notebook()

In [4]:
# Import packages
import pandas as pd
import numpy as np
import seaborn as sns
from pandasql import sqldf
pysqldf = lambda q: sqldf(q, globals())

In [5]:
# Set display to the full length

from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

# Panadas display options
pd.options.display.max_rows = 999
pd.options.display.max_columns = 999

In [6]:
funclass_translation = {'SILENT':'Synonymous','MISSENSE':'Non-synonymous','NONSENSE':'Stop','.':'Non-coding','NONE':'Indel'}
colors = {'Synonymous':'green','Non-synonymous':'orange','Stop':'red','Non-coding':'blue', 'Indel':'magenta'}

In [16]:
datasets = {
    'boston':
        [   
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/bos_by_sample_processed.tsv.gz',
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/bos_by_var_processed.tsv.gz'
        ],
    'cog-pre': 
        [   
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/cog-pre_by_sample_processed.tsv.gz',
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/cog-pre_by_var_processed.tsv.gz'
        ],
    'cog-post': 
        [   
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/cog-post_by_sample_processed.tsv.gz',
            'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/processed/cog-post_by_var_processed.tsv.gz'
        ]
}

In [7]:
# SARS-CoV-2 genome assembly url
gnm_url = 'https://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/009/858/895/GCF_009858895.2_ASM985889v3/GCF_009858895.2_ASM985889v3_genomic.gbff.gz'
gnm_file = gnm_url.split('/')[-1]

In [8]:
# Sites under selection URL
sel_url = 'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/selection/selection.tsv.gz'

In [9]:
# Get SARS-CoV-2 RefSeq genomes (in GenBank format) from NCBI
import os.path
from os import path
if not path.exists(gnm_file[:-3]):
    !wget -nc {gnm_url}
    !gunzip {gnm_file}
else:
    print('File {} is already here\nDoing nothing!'.format(gnm_file))

--2021-02-22 20:00:37--  https://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/009/858/895/GCF_009858895.2_ASM985889v3/GCF_009858895.2_ASM985889v3_genomic.gbff.gz
Resolving ftp.ncbi.nlm.nih.gov (ftp.ncbi.nlm.nih.gov)... 165.112.9.229, 2607:f220:41e:250::13, 2607:f220:41e:250::10, ...
Connecting to ftp.ncbi.nlm.nih.gov (ftp.ncbi.nlm.nih.gov)|165.112.9.229|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 24256 (24K) [application/x-gzip]
Saving to: ‘GCF_009858895.2_ASM985889v3_genomic.gbff.gz’

GCF_009858895.2_ASM 100%[===================>]  23.69K  --.-KB/s    in 0.01s   

2021-02-22 20:00:37 (1.91 MB/s) - ‘GCF_009858895.2_ASM985889v3_genomic.gbff.gz’ saved [24256/24256]



In [10]:
from Bio import SeqIO
genome = SeqIO.read(gnm_file[0:len(gnm_file)-3], "genbank")

In [11]:
# Variants of concern
voc_url = 'https://github.com/galaxyproject/SARS-CoV-2/raw/master/data/voc/voc.tsv.gz'

In [12]:
def create_hist(df,col,bins=100):
    hist, edges = np.histogram(df[col],bins)
    hist_df = pd.DataFrame({col: hist, "left": edges[:-1], "right": edges[1:]})
    hist_df["interval"] = ["%d to %d" % (left, right) for left, right in zip(hist_df["left"], hist_df["right"])]
    return(hist_df)

## Load the data

Available datasets are:

In [17]:
datasets.keys()

dict_keys(['boston', 'cog-pre', 'cog-post'])

In [18]:
dataset = 'boston'

In [19]:
var =   pd.read_csv(datasets[dataset][0],sep='\t')
sites = pd.read_csv(datasets[dataset][1],sep='\t')

## What's in the data?



In [ ]:
# Simple counts
tot_var = pysqldf('select count(*) from var').values[0][0]
tot_sites = len(pysqldf('select count(*) from var group by POS, change'))
tot_samples = pysqldf('select count(distinct Sample) from var').values[0][0]
print('There are {} variants across {} unique sites in {} samples.'.format(tot_var,tot_sites,tot_samples))

There are 38919 variants across 5760 unique sites in 1818 samples.


In [20]:
pysqldf('select type, count(*) from sites group by type')

type  count(*)
0  Indel        35
1    SNP       992

## Sample counts and thresholding

Here we assess how common variants are (how many samples contain each variant) and compute threshold of how many samples should share a variants for us to consider it in future analysis

In [21]:
#Distribution of sample counts
srcs = {}
counts = {}
sample_limit = 3
for func in var['FUNCLASS'].unique():
    srcs[func]=create_hist(sites[( sites['FUNCLASS']==func ) & ( sites['countunique(Sample)']>=sample_limit )],'countunique(Sample)',bins=60)
    counts[func] = len(sites[( sites['FUNCLASS']==func ) & ( sites['countunique(Sample)']>=sample_limit )])
plot = figure(plot_height = 300, plot_width = 400,
      title = "Sample counts per variant ({} variants)".format(np.sum([counts[key] for key in counts])),
      x_axis_label = '# Samples',
      y_axis_label = "Count",
      #y_axis_type='log'
      )  

for i,key in enumerate(srcs):
    plot.quad(bottom = 0, top = 'countunique(Sample)',left = "left", 
    right = "right", source = srcs[key], fill_color = colors[key], 
    line_color = "black", fill_alpha = 0.4,legend_label='{} ({})'.format(key, counts[key]))
plot.legend.click_policy="hide"
plot.legend.location = "top_center"

show(plot)


For thresholding we only select sites with allele frequencing between 1% and 50% because these are more likely to be erroneous than sites with allele frequencies between 50% and 100%.

In [22]:
# Count of sites present in 1, 2, 3, and so on samples
sc = pd.DataFrame(pysqldf('select POS, REF,ALT,count(distinct sample) as N from var where AF > .05 and AF <= .5 group by POS, REF,ALT order by N')['N'].value_counts()).reset_index()

In [23]:
# Add count of sites with 0 variants
sc = sc.append({"index":0,"N":len(genome)-len(var['POS'].unique())},ignore_index=True).sort_values(by=['index'])

In [24]:
# Lambda parameter for Poisson
l = len(var)/len(genome)

In [25]:
l

0.3093000702270675

In [26]:
# Computing poisson expectations
import math

def ps(l,s,N):
    el = math.exp(-l)
    lkf = 1
    i = 0
    sp = {'samples':[],'N':[]}
    while (el*lkf*N)>0.1:
        sp['samples'].append(i)
        sp['N'].append((el*lkf*N))
        i += 1
        lkf *= l/i
    return(sp)                 

In [27]:
estimate = ps(l,sc['index'].max(),len(genome))

In [28]:
from bokeh.models import Span
source = ColumnDataSource(estimate)
p = figure(plot_width=800, 
           plot_height=300,
           y_axis_type='log',
        x_axis_type='log',

           y_axis_label='# Individual variants',
           x_axis_label='# Samples sharing a variant',
            x_range=Range1d(start=1, end=100,bounds=(0, 100)),
            y_range=Range1d(start=0, end=100000,bounds=(0, 100000)),
           
           )
p.line(y='N',x='index',source=sc,line_color='red')
p.circle(y='N',x='index',source=sc,line_color='red')
p.line(x='samples',y='N',source=source,line_color='orange')

show(p)

The intersection of observed (red) and expected (yellow) lines above will give a threshold. 

In [29]:
# Set cutoff for subsequent analyses
s_cutoff = 2

In [30]:
# Add sample counts to by sample table 
var = pysqldf('select var.*,"countunique(Sample)" from var left join sites on var.POS = sites.POS and var.change = sites.change ')

In [31]:
# Apply cutoff to sites with AF < .5
var   = pd.concat( [ var[   (   var['countunique(Sample)']>=s_cutoff ) & (        var['AF']<=.5 ) ] ,          var[var['AF']>0.5] ] )
sites = pd.concat( [ sites[ ( sites['countunique(Sample)']>=s_cutoff ) & ( sites['max(AF)']<=.5 ) ] , sites[sites['max(AF)']>0.5] ] )

In [32]:
# Simple counts
tot_var = pysqldf('select count(*) from var').values[0][0]
tot_sites = len(pysqldf('select count(*) from var group by POS, change'))
tot_samples = pysqldf('select count(distinct Sample) from var').values[0][0]
print('There are {} variants across {} unique sites in {} samples.'.format(tot_var,tot_sites,tot_samples))

There are 9061 variants across 839 unique sites in 639 samples.


#### Categories of variants

In [33]:
#Distribution of allele frequencies
colors = {'Synonymous':'green','Non-synonymous':'orange','Stop':'red','Non-coding':'blue', 'Indel':'magenta'}

srcs = {}

for func in var['FUNCLASS'].unique():
    srcs[func]=create_hist(var[var['FUNCLASS']==func],'AF')

plot = figure(plot_height = 300, plot_width = 800,
      title = "Histogram of Allele Frequencies for {} dataset".format(dataset.capitalize()),
      x_axis_label = 'AF',
      y_axis_label = "Count")  

for i,key in enumerate(srcs):
    plot.quad(bottom = 0, top = 'AF',left = "left", 
    right = "right", source = srcs[key], fill_color = colors[key], 
    line_color = "black", fill_alpha = 0.4,legend_label='{} ({})'.format(key,len(sites[sites['FUNCLASS']==key]['FUNCLASS'])))
plot.legend.click_policy="hide"
plot.legend.location = "top_center"

show(plot)

try:
    r = dp.Report(
        dp.Plot(plot)
        )
    r.publish(name='AF versus Samples in {} dataset'.format(dataset), open=True)
except:
    print('Did you initialize DataPane?')


Did you initialize DataPane?


In [34]:
len(var)

9061

In [35]:
for bounds in [[0,0.1],[0.1,0.8],[0.8,1]]:
    print(pysqldf('select Sample, count(*) as "{0}-{1}" from var where AF >= {0} and AF < {1} and "countunique(Sample)">=5 group by Sample '.format(bounds[0],bounds[1])).describe().loc[['count','mean','min','max']].T.to_markdown())

|       |   count |    mean |   min |   max |
|:------|--------:|--------:|------:|------:|
| 0-0.1 |     578 | 5.48616 |     1 |    29 |
|         |   count |    mean |   min |   max |
|:--------|--------:|--------:|------:|------:|
| 0.1-0.8 |     204 | 2.69118 |     1 |    17 |
|       |   count |    mean |   min |   max |
|:------|--------:|--------:|------:|------:|
| 0.8-1 |     639 | 7.15493 |     1 |    13 |


### Distribution of variant AFs across samples.


In [36]:
af_stat = var.groupby(['POS','change'])['AF'].describe()

In [37]:
af_stat['CoV']=af_stat['std']/af_stat['mean']
af_stat.fillna(0,inplace=True)

In [38]:
sites = pysqldf('select sites.*, CoV,mean from sites left join af_stat on sites.POS = af_stat.POS and sites.change = af_stat.change ')

In [39]:
for key in colors:
    sites.loc[(sites['FUNCLASS']==key),'color'] = colors[key]
    var.loc[(var['FUNCLASS']==key),'color'] = colors[key]

In [40]:
sites.head()

POS   REF ALT    IMPACT        FUNCLASS                            EFFECT  \
0  159     G   T         .      Non-coding                                 .   
1  457     G   C  MODERATE  Non-synonymous             NON_SYNONYMOUS_CODING   
2  458     A   T  MODERATE  Non-synonymous             NON_SYNONYMOUS_CODING   
3  506     A   C  MODERATE  Non-synonymous             NON_SYNONYMOUS_CODING   
4  514  GTTA   G  MODERATE           Indel  CODON_CHANGE_PLUS_CODON_DELETION   

     GENE       CODON     AA    TRID  countunique(Sample)   min(AF)   max(AF)  \
0       .           .      .       .                  570  0.006707  0.250000   
1  ORF1ab     Gaa/Caa   E65Q  leader                  343  0.001726  0.112069   
2  ORF1ab     gAa/gTa   E65V  leader                  344  0.001565  0.119658   
3  ORF1ab     cAt/cCt   H81P  leader                    2  0.001048  0.128015   
4  ORF1ab  gttatg/gtg  VM84V  leader                   84  0.000387  0.176801   

                           SAMPLES(above-thresholds)  \
0  SRR11953759,SRR11953765,SRR11953767,SRR1195380...   
1                SRR11953813,SRR11953821,SRR11953939   
2                SRR11953813,SRR11953821,SRR11953939   
3                                        SRR12733663   
4                                        SRR11953746   

                                        SAMPLES(all)  \
0  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
1  SRR12733283,SRR12733284,SRR12733290,SRR1273329...   
2  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
3                            SRR12733663,SRR11954196   
4  SRR12733296,SRR12733308,SRR12733315,SRR1273332...   

                                            AFs(all)  change  fel_p  meme_p  \
0  0.033777,0.037259,0.034504,0.040725,0.037567,0...     G>T    NaN     NaN   
1  0.002741,0.004344,0.005138,0.00509,0.006324,0....     G>C    NaN     NaN   
2  0.002699,0.004107,0.003367,0.005199,0.004986,0...     A>T    NaN     NaN   
3                                  0.128015,0.001048     A>C    NaN     NaN   
4  0.001924,0.029683,0.001796,7.93E-4,0.00126,0.0...  GTTA>G    NaN     NaN   

   freq B1351    P1  B117 BLOOM  A321   type       CoV      mean    color  
0   NaN  None  None  None  None  None    SNP  0.360958  0.075054     blue  
1   NaN  None  None  None  None  None    SNP  0.329943  0.081297   orange  
2   NaN  None  None  None  None  None    SNP  0.350817  0.085161   orange  
3   NaN  None  None  None  None  None    SNP  0.000000  0.128015   orange  
4   NaN  None  None  None  None  None  Indel  0.000000  0.176801  magenta

In [41]:
sites['frac'] = sites['countunique(Sample)']/var['Sample'].nunique()

In [42]:
from bokeh.layouts import row

af_cov_sample = ColumnDataSource(sites.rename(columns={"countunique(Sample)": "samples"}))

TOOLTIPS_p1 = [
    ("(mean,cov)", "(@mean, @CoV)")
]

TOOLTIPS_p2 = [
               ("(mean,PF)", "(@mean, @frac)")
]

p1 = figure(
    plot_height = 400, plot_width = 400,
    title = "Mean AF versus coefficient of variation for AF",
    y_axis_label = 'Coefficient of Variation for AF',
    x_axis_label = "Mean AF",
    tooltips=TOOLTIPS_p1,
    #tools='save'
    )

p1.circle(
    y='CoV',
    x='mean',
    color='color',
    alpha=.5,
    source=af_cov_sample,
    size=8
    )

p2 = figure(
    plot_height = 400, 
    plot_width = 400,
    title = "CoV versus PF",
    x_axis_label = 'Fraction of samples containing a variant (aka PF)',
    y_axis_label = 'Coefficient of Variation for AF',
    tooltips=TOOLTIPS_p2,
    y_range=p1.y_range
    #tools='save'
    )
        
p2.circle(
    x='CoV',
    y='mean',
    line_color=None,
    fill_color='color',
    alpha=.5,
    source=af_cov_sample,
    size=8
    )

try:
    bokeh.io.reset_output()
    bokeh.io.output_notebook()
    bokeh.io.show(row(p1,p2))
except:
    bokeh.io.output_notebook()
    bokeh.io.show(row(p1,p2))

try:
    r = dp.Report(
        dp.Group(
            dp.Plot(p1),
            dp.Plot(p2),
            columns=2
        )
    )
    r.publish(name='AF versus Samples in {} dataset'.format(dataset), open=True)
except:
    print("Did you initialize DataPane?")

Did you initialize DataPane?


In [43]:
pysqldf('select * from sites where "countunique(Sample)" > 100 and "max(AF)"<0.5 order by "countunique(Sample)" desc').head(10)

POS REF ALT    IMPACT        FUNCLASS                 EFFECT    GENE  \
0  12925   A  AC      HIGH           Indel            FRAME_SHIFT  ORF1ab   
1  26056   A   C  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING   ORF3a   
2  15070   T   A  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
3  29038   A   T      HIGH            Stop            STOP_GAINED       N   
4   5764   G   A  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
5   5765   G   C  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
6   7506   A   C  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
7  15681   T   A  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
8  13692   A   T  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   
9  18847   C   G  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   

      CODON      AA   TRID  countunique(Sample)   min(AF)   max(AF)  \
0  aaa/aCaa   K81T?   nsp9                  631  0.004034  0.253731   
1   gAc/gCc   D222A  orf3a                  624  0.009505  0.253165   
2   cTt/cAt   L544H   RdRp                  622  0.006390  0.296296   
3   Aag/Tag   K256*      N                  618  0.012000  0.172840   
4   Ggt/Agt  G1016S   nsp3                  617  0.014927  0.222892   
5   gGt/gCt  G1016A   nsp3                  616  0.013817  0.222892   
6   aaA/aaC  K1596N   nsp3                  611  0.010309  0.144928   
7   Tat/Aat   Y748N   RdRp                  610  0.009865  0.136289   
8   Aca/Tca    T85S   RdRp                  608  0.017260  0.428571   
9   gCt/gGt   A270G   ExoN                  607  0.003852  0.104089   

                           SAMPLES(above-thresholds)  \
0  SRR11953673,SRR11953682,SRR11953683,SRR1195368...   
1  SRR11953691,SRR11953700,SRR11953726,SRR1195380...   
2  SRR11953670,SRR11953691,SRR11953700,SRR1195377...   
3  SRR11953679,SRR11953682,SRR11953696,SRR1195370...   
4  SRR11953691,SRR11953701,SRR11953726,SRR1195375...   
5  SRR11953691,SRR11953701,SRR11953726,SRR1195399...   
6  SRR11953679,SRR11953682,SRR11953691,SRR1195370...   
7  SRR11953678,SRR11953679,SRR11953682,SRR1195370...   
8  SRR11953676,SRR11953726,SRR11953855,SRR1195386...   
9  SRR11953682,SRR11953691,SRR11953700,SRR1195371...   

                                        SAMPLES(all)  \
0  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
1  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
2  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
3  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
4  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
5  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
6  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
7  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
8  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   
9  SRR12733283,SRR12733284,SRR12733288,SRR1273329...   

                                            AFs(all) change  fel_p  meme_p  \
0  0.013487,0.02016,0.033748,0.03605,0.041441,0.0...   A>AC    NaN     NaN   
1  0.030862,0.033046,0.029538,0.049,0.030425,0.03...    A>C    NaN     NaN   
2  0.01565,0.031968,0.026567,0.048919,0.015863,0....    T>A    NaN     NaN   
3  0.111768,0.107932,0.086957,0.037932,0.082803,0...    A>T    NaN     NaN   
4  0.050568,0.076569,0.081761,0.053753,0.072368,0...    G>A    NaN     NaN   
5  0.051363,0.077738,0.085227,0.053494,0.078172,0...    G>C    NaN     NaN   
6  0.034498,0.044643,0.048829,0.058948,0.043922,0...    A>C    NaN     NaN   
7  0.091951,0.086657,0.075904,0.025159,0.079559,0...    T>A    NaN     NaN   
8  0.034559,0.053793,0.064733,0.059213,0.045969,0...    A>T    NaN     NaN   
9  0.008626,0.011788,0.012009,0.019728,0.013248,0...    C>G    NaN     NaN   

   freq B1351    P1  B117 BLOOM  A321   type       CoV      mean    color  \
0   NaN  None  None  None  None  None  Indel  0.443153  0.088993  magenta   
1   NaN  None  None  None  None  None    SNP  0.386512  0.086460   orange   
2   NaN  None  None  None  None  None    SNP  0.601

In [44]:
import scipy.stats as stats
# non-parametric pdf
site = 23085
af = var[var['POS']==site]['AF']
nparam_density = stats.kde.gaussian_kde(af.values.ravel())
x = np.linspace(0, 1, 100)
pdf = nparam_density(x)
plot = figure(plot_height = 200, plot_width = 800,
    title = 'Site {} ({} Samples)'.format(site,len(af)),
    x_axis_label = 'AF',
    y_axis_label = "Density",
    x_range=Range1d(start=0, end=1,bounds=(0, 1)),
    y_range=Range1d(start=0, end=5,bounds=(0, 30)),
    toolbar_location="below"
    )  
#for value in af.values.ravel():
#    plot.line(x=[value,value],y=[-.5,.5],line_color='red')
ticks = ColumnDataSource({'tick':af.values.ravel()})
plot.line(x=x, y=pdf,line_color='black')
plot.varea(x=x, y1=pdf,fill_color='orange',alpha=.6)
#plot.line(x=['tick','tick'],y=[-.5,.5],line_color='red',source=ticks)
glyph = Rect(x='tick',y=0,width=0.0001, height=1,line_color='red',line_alpha=.5)
plot.add_glyph(ticks,glyph)
#    plots.append(plot)
show(plot)

In [46]:
from datetime import date

source = ColumnDataSource(sites.rename(columns={"countunique(Sample)": "samples","min(AF)":"mAF","max(AF)":"xAF"}))
TOOLTIPS = [
    ("Position", "@POS"),
    ("GENE","@TRID"),
    ("min(AF)","@mAF"),
    ("max(AF)","@xAF"),
    ("# samples","@samples")
]
p = figure(plot_height=200,
        plot_width=1200,
        y_range=sorted(sites['FUNCLASS'].unique(),key=str.lower),
        tooltips = TOOLTIPS,
        x_range=Range1d(start=0, end=30000,bounds=(0, 30000)),
        )
glyph_p = Rect(x='POS',y='FUNCLASS',width=10, height='CoV')
p.add_glyph(source,glyph_p)
show(p)

try:
    r = dp.Report(
        dp.Plot(p)
    )
    r.publish(name='Spatial distribution in {} data'.format(dataset), open=True)
except:
    print("Did you initialize datapane?")                    


Did you initialize datapane


In [47]:
by_gene_fc = pysqldf('select FUNCLASS, TRID, avg(AF) as AF, avg(AF)*20 as AF_scaled, count(distinct POS) as count, min(POS) as pos from var group by TRID,FUNCLASS order by pos')

In [48]:
by_gene_type = pysqldf('select type, TRID, avg(AF)*20 as AF, count(distinct POS) as count, min(POS) as pos from var group by TRID,type order by pos')

In [49]:
by_gene_fc.head()

FUNCLASS    TRID        AF  AF_scaled  count  pos
0      Non-coding       .  0.866637  17.332744     39   12
1      Synonymous  leader  0.832735  16.654696      6  270
2  Non-synonymous  leader  0.490669   9.813379      5  457
3           Indel  leader  0.797425  15.948498      6  506
4      Synonymous    nsp2  0.712772  14.255436     20  822

In [50]:
from bokeh.palettes import cividis
from bokeh.models import ColorBar
from bokeh.transform import linear_cmap
from math import pi

source = ColumnDataSource(by_gene_fc)
mapper = linear_cmap(field_name='count', palette=cividis(len(by_gene_fc['count'])) ,low=min(by_gene_fc['count'].unique()) ,high=max(by_gene_fc['count'].unique()))

TOOLTIPS = [
    ("Distinct variants", "@count"),
    ("mean AF","@AF")
]

p = figure(plot_height=200,
           plot_width=800,
           y_range=sorted(by_gene_fc['FUNCLASS'].unique(),key=str.lower),
           x_range=by_gene_fc['TRID'].unique(),
           x_axis_label = 'Genes',
           title = "Variants per gene (circle size = average AF, color = number of distinct variants)",
           tools='save',
           tooltips = TOOLTIPS
           )
p.circle(x='TRID',
         color=mapper,
         y='FUNCLASS',
         size='AF_scaled',
         source=source,
         alpha=.4
         )
color_bar = ColorBar(color_mapper=mapper['transform'], width=8,  location=(0,0))
p.add_layout(color_bar, 'right')
p.xaxis.major_label_orientation = pi/2



try:
    bokeh.io.reset_output()
    bokeh.io.output_notebook()
    bokeh.io.show(p)
except:
    bokeh.io.output_notebook()
    bokeh.io.show(p)

try:
    r = dp.Report(
        dp.Plot(p)
    )
    r.publish(name='Variants across genes in {} dataset'.format(dataset), open=True)
except:
    print("Did you initialize datapane?")



Did you initialize datapane?


## VOC

In [51]:
voc = pd.read_csv(voc_url, sep='\t', header=None, names=['set','aa','position'])

In [52]:
voc_axis = pysqldf('select "set" || "/" || aa as id from voc order by "set", position')

In [53]:
voc  = pysqldf('select voc.*, "countunique(Sample)", CoV, GENE from voc left join sites on POS >= position and POS < position+3 order by "set",position')

In [54]:
voc = pysqldf('select  "set" || "/" || aa as id, * from voc order by "set", position')

In [55]:
#Making glyphs visible
size_factor = 50

In [56]:
voc['frac']=(voc['countunique(Sample)']/var['Sample'].nunique())*size_factor

In [57]:
pysqldf('select * from sites where POS = 27972')

Empty DataFrame
Columns: [POS, REF, ALT, IMPACT, FUNCLASS, EFFECT, GENE, CODON, AA, TRID, countunique(Sample), min(AF), max(AF), SAMPLES(above-thresholds), SAMPLES(all), AFs(all), change, fel_p, meme_p, freq, B1351, P1, B117, BLOOM, A321, type, CoV, mean, color, frac]
Index: []

In [58]:
voc

id    set       aa  position  countunique(Sample)       CoV  \
0     A321/F157L   A321    F157L     22030                  NaN       NaN   
1     A321/V367F   A321    V367F     22660                  NaN       NaN   
2     A321/Q613H   A321    Q613H     23398                  NaN       NaN   
3      A321/P681   A321     P681     23602                  NaN       NaN   
4    B117/T1001I   B117   T1001I      3265                  NaN       NaN   
5    B117/A1708D   B117   A1708D      5386                  NaN       NaN   
6    B117/I2230T   B117   I2230T      6952                  NaN       NaN   
7      B117/del9   B117     del9     11288                  NaN       NaN   
8      B117/del6   B117     del6     21765                  3.0  0.000000   
9      B117/del3   B117     del3     21991                  7.0  0.038697   
10     B117/del3   B117     del3     21991                  1.0  0.000000   
11    B117/N501Y   B117    N501Y     23062                  NaN       NaN   
12    B117/A570D   B117    A570D     23269                  1.0  0.000000   
13    B117/P681H   B117    P681H     23602                  NaN       NaN   
14    B117/T716I   B117    T716I     23707                  NaN       NaN   
15    B117/S982A   B117    S982A     24505                  NaN       NaN   
16   B117/D1118H   B117   D1118H     24913                  NaN       NaN   
17  B117/Q27stop   B117  Q27stop     27971                  2.0  0.000000   
18     B117/Y73C   B117     Y73C     28109                  NaN       NaN   
19      B117/D3L   B117      D3L     28279                  NaN       NaN   
20    B117/S235F   B117    S235F     28975                  NaN       NaN   
21  B1351/K1655N  B1351   K1655N      5227                  NaN       NaN   
22    B1351/D80A  B1351     D80A     21799                  NaN       NaN   
23   B1351/D215G  B1351    D215G     22204                  NaN       NaN   
24   B1351/K417N  B1351    K417N     22810                  NaN       NaN   
25   B1351/E484K  B1351    E484K     23011                  NaN       NaN   
26   B1351/N501Y  B1351    N501Y     23062                  NaN       NaN   
27   B1351/A701V  B1351    A701V     23662                  NaN       NaN   
28    B1351/P71L  B1351     P71L     26454                  2.0  0.000000   
29   B1351/T205I  B1351    T205I     28885                 13.0  0.872875   
30    BLOOM/Y365  BLOOM     Y365     22654                  NaN       NaN   
31    BLOOM/Y369  BLOOM     Y369     22666                  NaN       NaN   
32    BLOOM/S383  BLOOM     S383     22708                  NaN       NaN   
33    BLOOM/P384  BLOOM     P384     22711                  NaN       NaN   
34    BLOOM/S443  BLOOM     S443     22888                  NaN       NaN   
35    BLOOM/K444  BLOOM     K444     22891                  NaN       NaN   
36    BLOOM/V445  BLOOM     V445     22894                  NaN       NaN   
37    BLOOM/G446  BLOOM     G446     22897                  1.0  0.000000   
38    BLOOM/G447  BLOOM     G447     22900                  NaN       NaN   
39    BLOOM/N448  BLOOM     N448     22903                  NaN       NaN   
40    BLOOM/Y449  BLOOM     Y449     22906                  NaN       NaN   
41    BLOOM/N450  BLOOM     N450     22909                  NaN       NaN   
42    BLOOM/L455  BLOOM     L455     22924                  NaN       NaN   
43    BLOOM/F456  BLOOM     F456     22927                  NaN       NaN   
44    BLOOM/I472  BLOOM     I472     22975                  NaN       NaN   
45    BLOOM/Y473  BLOOM     Y473     22978                  NaN       NaN   
46    BLOOM/E484  BLOOM     E484     23011                  NaN       NaN   
47    BLOOM/G485  BLOOM     G485     23014                  NaN       NaN   
48    BLOOM/F486  BLOOM     F486     23017                  NaN       NaN   
49    BLOOM/F490  BLOOM     F490     23029                  1.0  0.000000   
50    BLOOM/G496  BLOOM     G496     23047                  NaN       NaN   
51     P1/

In [59]:
voc_var = pysqldf('select var.*, "set" from var join voc on POS >= position and POS < position+3 order by "set",position')

In [60]:
voc_sites = pysqldf('select sites.*, "set" from sites join voc on POS >= position and POS < position+3 order by "set",position')

In [61]:
var.head()

Sample    POS FILTER REF ALT    DP        AF   SB            DP4  \
1   SRR11953670  15070   PASS   T   A   114  0.087719   30     39,64,10,1   
10  SRR11953673   3466   PASS   G   T  1356  0.050147  132  439,838,61,18   
11  SRR11953673   4228   PASS   A   C  1234  0.054295  154  379,782,59,14   
12  SRR11953673  12412   PASS   A   C  1096  0.058394  138  378,650,57,11   
13  SRR11953673  12925   PASS   A  AC   988  0.051619  117   432,505,48,3   

      IMPACT        FUNCLASS                 EFFECT    GENE     CODON     AA  \
1   MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   cTt/cAt  L544H   
10      HIGH            Stop            STOP_GAINED  ORF1ab   Gga/Tga  G250*   
11  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   Aca/Cca  T504P   
12  MODERATE  Non-synonymous  NON_SYNONYMOUS_CODING  ORF1ab   Aac/Cac  N108H   
13      HIGH           Indel            FRAME_SHIFT  ORF1ab  aaa/aCaa  K81T?   

    TRID   min(AF)   max(AF)  countunique(change)  countunique(FUNCLASS)  \
1   RdRp  0.006390  0.296296                    1                      1   
10  nsp3  0.004189  0.117188                    1                      1   
11  nsp3  0.005070  0.136364                    1                      1   
12  nsp8  0.004820  0.428571                    1                      1   
13  nsp9  0.004034  0.253731                    1                      1   

   change   type  countunique(Sample)    color  
1     T>A    SNP                  622   orange  
10    G>T    SNP                  504      red  
11    A>C    SNP                  534   orange  
12    A>C    SNP                  590   orange  
13   A>AC  Indel                  631  magenta

In [62]:
from bokeh.palettes import Turbo256, linear_palette
palette = linear_palette(Turbo256,(len(var['GENE'].unique())))
gene_colors = {}
for i, gene in enumerate(var['GENE'].unique()):
    gene_colors[gene] = palette[i]

In [63]:
for gene in voc['GENE'].unique():
    if gene is not None:
        voc.loc[voc['GENE']==gene,'color'] = gene_colors[gene]

In [64]:
line_ends = {}
for mut_set in voc['set'].unique():
    start = voc[ voc['set']==mut_set ]['position'].min()
    end   = voc[ voc['set']==mut_set ]['position'].max()
    a = pysqldf('select id from voc where "set" = "{}" and position = {}'.format(mut_set,start)).iloc[0][0]
    b = pysqldf('select id from voc where "set" = "{}" and position = {}'.format(mut_set,end)).iloc[0][0]
    line_ends[mut_set]=[a,b]

In [65]:
line_ends

{'A321': ['A321/F157L', 'A321/P681'],
 'B117': ['B117/T1001I', 'B117/S235F'],
 'B1351': ['B1351/K1655N', 'B1351/T205I'],
 'BLOOM': ['BLOOM/Y365', 'BLOOM/G496'],
 'P1': ['P1/S1188L', 'P1/P80R']}

In [66]:
voc.dropna(how='any')

id    set       aa  position  countunique(Sample)       CoV  \
8      B117/del6   B117     del6     21765                  3.0  0.000000   
9      B117/del3   B117     del3     21991                  7.0  0.038697   
10     B117/del3   B117     del3     21991                  1.0  0.000000   
12    B117/A570D   B117    A570D     23269                  1.0  0.000000   
17  B117/Q27stop   B117  Q27stop     27971                  2.0  0.000000   
28    B1351/P71L  B1351     P71L     26454                  2.0  0.000000   
29   B1351/T205I  B1351    T205I     28885                 13.0  0.872875   
37    BLOOM/G446  BLOOM     G446     22897                  1.0  0.000000   
49    BLOOM/F490  BLOOM     F490     23029                  1.0  0.000000   
54       P1/L18F     P1     L18F     21613                  3.0  0.501646   

    GENE      frac    color  
8      S  0.234742  #4353c2  
9      S  0.547731  #4353c2  
10     S  0.078247  #4353c2  
12     S  0.078247  #4353c2  
17  ORF8  0.156495  #27eda3  
28     E  0.156495  #f0cb3a  
29     N  1.017214  #78fe59  
37     S  0.078247  #4353c2  
49     S  0.078247  #4353c2  
54     S  0.234742  #4353c2

In [68]:
from bokeh.models import Legend
from bokeh.transform import linear_cmap
from math import pi
from bokeh.transform import factor_cmap
from bokeh.models import BoxAnnotation, Toggle

source = ColumnDataSource(voc.dropna(how='any').rename(columns={"countunique(Sample)": "samples"}))
TOOLTIPS = [
            ("# samples","@samples"),
            ("Set","@set"),
            ("Mutation","@aa"),
            ("Position","@position")
]

p = figure(plot_height=300,
    plot_width=1000,
    x_range=voc['id'].unique(),
    x_axis_label = 'VOC Set/Change',
    y_axis_label = 'Coef of Var for AF',
    tooltips=TOOLTIPS,
    title = "VOCs in {} data (Size ∝ Fraction of samples containing variant; [min;max] = [{:.0f},{:.0f}] out of {})".format(dataset.capitalize(),
                                                                                                                    voc['countunique(Sample)'].min(),
                                                                                                                    voc['countunique(Sample)'].max(),
                                                                                                                    var['Sample'].nunique()
    )
    )
p.add_layout(Legend(), 'right')

p.circle(x='id',
    color='color',
    y='CoV',
    radius='frac',
    source=source,
    legend_field="GENE",
    alpha=.5
    )

for i,mut_set in enumerate(voc['set'].unique()):
    p.line([line_ends[mut_set][0],line_ends[mut_set][1]], [-.1, -.1], line_color=Reds[5][i],width=10)

p.ygrid.grid_line_color = None
orientation = pi/2
p.legend.location = "top_center"
p.xaxis.major_label_orientation = pi/2

try:
    bokeh.io.reset_output()
    bokeh.io.output_notebook()
    bokeh.io.show(p)
except:
    bokeh.io.output_notebook()
    bokeh.io.show(p)

try:
    voc.dropna(how='any')
    r = dp.Report(
        dp.DataTable(voc.dropna(how='any'))
    )
    r.publish(name='Variants of Concern in {} dataset'.format(dataset))
except:
    print("Did you initialize DataPane?")
                    


Did you initialize DataPane?
